In [8]:
from collections import Counter
import datetime
import pathlib
import re
from typing import Optional, Tuple

import pandas as pd


class Parser:
    CHUNKSIZE = 1e3

    def __init__(self, df: str):
        self._df = df
        self._kind = None
        self._name_col = None
        self._postal_codes = {
            int(row["INDEX"]): (row["REGION"], row["CITY"])
            for _, row in pd.read_csv(
                pathlib.Path(".").parent / "../backend/app/assets/postal-codes.csv",
                
            ).iterrows()
        }

    def _detect_kind_and_name_col(
        self, chunk: pd.DataFrame
    ) -> Tuple[Optional[int], Optional[str]]:
        name_cols = {
            "invention name": 1,
            "utility model name": 2,
            "industrial design name": 3,
        }

        for option in name_cols:
            if option in chunk.columns:
                name_col = option
                break
        else:
            return None, None

        return name_cols[name_col], name_col

    def _parse_row(self, row: pd.Series) -> dict:
        row = row.fillna("")
        
        reg_number = row.get("registration number")
        if reg_number is None:
            return None        
        elif reg_number.isdigit():
            reg_number = int(reg_number)
        else:
            reg_number = re.search("\d+", reg_number)
            if reg_number is not None:
                reg_number = int(reg_number[0])
            else:
                return None

        try:
            reg_date = datetime.datetime.strptime(
                row.get("registration date"), "%Y%m%d").date()
        except ValueError:
            reg_date = None

        try:
            appl_date = datetime.datetime.strptime(
                row.get("application date"), "%Y%m%d").date()
        except ValueError:
            appl_date = None

        author_raw = row.get("authors", "")
        owner_raw = row.get("patent holders", "")
        address = row.get("correspondence address", "")
        name = row.get(self._name_col, "")

        actual = row.get("actual", True)

        kind = self._kind
        
        category, subcategory = None, None
        if kind in (1, 2):
            class_code = row.get("mpk")
            if class_code:
                category = ", ".join([c.strip()[:3] for c in class_code.split(":")])
                subcategory = ", ".join([c.strip()[:4] for c in class_code.split(":")])

        country_code_regex = re.compile("\((?a:\w{2})\)")
        country_codes = Counter(country_code_regex.findall(owner_raw))
        if len(country_codes) == 0 or "(RU)" in country_codes:
            country_code = "RU"
        elif len(country_codes) == 1:
            country_code = list(country_codes)[0][1:-1]
        else:
            country_code = country_codes.most_common(1)[0][0][1:-1]
        
        postal_code_regex = re.compile("\d{6}")
        postal_code = postal_code_regex.search(address)
        region, city = None, None
        if postal_code is not None:
            try:
                postal_code = int(postal_code[0])
                region, city = self._postal_codes.get(postal_code, (None, None))
            except Exception:
                pass

        author_count = len(author_raw.split("\r\n"))

        return dict(
            reg_number=reg_number,
            reg_date=reg_date,
            appl_date=appl_date,
            author_raw=author_raw,
            owner_raw=owner_raw,
            address=address,
            name=name,
            actual=actual,
            category=category,
            subcategory=subcategory,
            kind=kind,
            country_code=country_code,
            region=region,
            city=city,
            author_count=author_count,
        )

    def parse(self):
        df = pd.read_csv(self._df, dtype=str, chunksize=self.CHUNKSIZE)

        for chunk in df:
            chunk.drop_duplicates(subset=["registration number"], inplace=True)
            for _, row in chunk.iterrows():
                data = self._parse_row(row)
                yield data

    def setup(self):
        df = pd.read_csv(self._df, chunksize=self.CHUNKSIZE)
        chunk = df.get_chunk(1)

        if "registration number" not in chunk.columns:
            print("Column 'Registration number' not found in data")
            return False

        kind, name_col = self._detect_kind_and_name_col(chunk)
        if kind is None or name_col is None:
            print("Cannot detect kind and name col")
            return False

        self._kind = kind
        self._name_col = name_col

        return True

In [9]:
parser = Parser("../data/opendata/designs.csv")
parser.setup()

True

In [10]:
for res in parser.parse():
    print(res)


{'reg_number': 38001, 'reg_date': datetime.date(1993, 2, 22), 'appl_date': datetime.date(1992, 1, 9), 'author_raw': 'Милорава Т В (RU)', 'owner_raw': 'Т.В.Милорава (RU)', 'address': '', 'name': 'ТЕНПУРИ (два варианта)', 'actual': 'false', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'RU', 'region': None, 'city': None, 'author_count': 1}
{'reg_number': 38002, 'reg_date': datetime.date(1993, 2, 22), 'appl_date': datetime.date(1992, 1, 3), 'author_raw': 'Милорава Т В (RU)', 'owner_raw': 'Т.В.Милорава (RU)', 'address': '', 'name': 'ТЕНПУРИ (два варианта)', 'actual': 'false', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'RU', 'region': None, 'city': None, 'author_count': 1}
{'reg_number': 38003, 'reg_date': datetime.date(1993, 2, 22), 'appl_date': datetime.date(1991, 9, 30), 'author_raw': 'Кудинова Т А (RU)', 'owner_raw': 'Малое предприятие "Караван", Москва (RU)', 'address': '', 'name': 'КУРТКА МУЖСКАЯ', 'actual': 'false', 'category': None, 'subcat

{'reg_number': 38224, 'reg_date': datetime.date(1993, 5, 28), 'appl_date': datetime.date(1991, 9, 19), 'author_raw': 'Алипова И М (RU)', 'owner_raw': 'Акционерное общество "Курская обувь" (RU)', 'address': '', 'name': 'ТУФЛИ ЖЕНСКИЕ', 'actual': 'false', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'RU', 'region': None, 'city': None, 'author_count': 1}
{'reg_number': 38225, 'reg_date': datetime.date(1993, 5, 28), 'appl_date': datetime.date(1991, 10, 30), 'author_raw': 'Попова О А (RU)', 'owner_raw': 'Акционерное общество закрытого типа "Восток", Москва (RU)', 'address': '', 'name': 'САПОГИ ЖЕНСКИЕ', 'actual': 'false', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'RU', 'region': None, 'city': None, 'author_count': 1}
{'reg_number': 38226, 'reg_date': datetime.date(1993, 5, 28), 'appl_date': datetime.date(1991, 10, 30), 'author_raw': 'Бочина Н И (RU)', 'owner_raw': 'Акционерное общество закрытого типа "Восток", Москва (RU)', 'address': '', 'name':

{'reg_number': 38483, 'reg_date': datetime.date(1993, 5, 28), 'appl_date': datetime.date(1992, 7, 24), 'author_raw': 'Сильковский А П (UA)', 'owner_raw': 'А.П.Сильковский (UA)', 'address': '', 'name': 'ПРОФИЛОМЕТР ЛАЗЕРНЫЙ', 'actual': 'false', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'UA', 'region': None, 'city': None, 'author_count': 1}
{'reg_number': 38484, 'reg_date': datetime.date(1993, 5, 28), 'appl_date': datetime.date(1992, 7, 20), 'author_raw': 'Нефедов Б Д (RU)', 'owner_raw': 'Научно-исследовательский технологический институт, Рязань (RU)', 'address': '', 'name': 'ТЕРМОМЕТР ЭЛЕКТРОННЫЙ', 'actual': 'false', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'RU', 'region': None, 'city': None, 'author_count': 1}
{'reg_number': 38485, 'reg_date': datetime.date(1993, 5, 28), 'appl_date': datetime.date(1992, 7, 27), 'author_raw': 'Лоскутов А Н (RU)', 'owner_raw': 'А.Н.Лоскутов (RU)', 'address': '', 'name': 'СЧЕТЧИК КРЫЛЬЧАТЫЙ ХОЛОДНОЙ ВОДЫ', 

{'reg_number': 38726, 'reg_date': datetime.date(1993, 5, 28), 'appl_date': datetime.date(1992, 7, 2), 'author_raw': 'Ефремова С В (RU)', 'owner_raw': 'Кооператив "Клуб мастеров", Москва (RU)', 'address': '', 'name': 'ИГРУШКА "ОБЕЗЬЯНА БИЛЛ"', 'actual': 'false', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'RU', 'region': None, 'city': None, 'author_count': 1}
{'reg_number': 38727, 'reg_date': datetime.date(1993, 5, 28), 'appl_date': datetime.date(1992, 5, 28), 'author_raw': 'Васильев В Н (RU)', 'owner_raw': 'В.Н.Васильев (RU)', 'address': '', 'name': 'ИГРА НАСТОЛЬНАЯ "РОБОТЫ ПОЛИЦЕЙСКИЕ"', 'actual': 'false', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'RU', 'region': None, 'city': None, 'author_count': 1}
{'reg_number': 38728, 'reg_date': datetime.date(1993, 5, 28), 'appl_date': datetime.date(1992, 7, 14), 'author_raw': 'Кунщикова Е Л (RU)', 'owner_raw': 'Акционерное общество "Протон", Орел (RU)', 'address': '', 'name': 'ИГРА ЭЛЕКТРОННАЯ (два 

{'reg_number': 38999, 'reg_date': datetime.date(1993, 8, 30), 'appl_date': datetime.date(1992, 12, 30), 'author_raw': 'Купервассер А М (RU)', 'owner_raw': 'Научно-исследовательский институт текстильных материалов, Москва (RU)', 'address': '', 'name': 'ГАЛСТУК', 'actual': 'false', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'RU', 'region': None, 'city': None, 'author_count': 1}
{'reg_number': 39000, 'reg_date': datetime.date(1993, 8, 30), 'appl_date': datetime.date(1991, 9, 2), 'author_raw': 'Кудрина Т М (RU)', 'owner_raw': 'Государственная академия сферы быта и услуг, Москва (RU)', 'address': '', 'name': 'НАБОР ШКАТУЛОК', 'actual': 'false', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'RU', 'region': None, 'city': None, 'author_count': 1}
{'reg_number': 39001, 'reg_date': datetime.date(1993, 8, 30), 'appl_date': datetime.date(1992, 1, 9), 'author_raw': 'Крашенинникова Т Б (RU)', 'owner_raw': 'Т.Б.Крашенинникова (RU)', 'address': '', 'name': 'С

...

{'reg_number': 50043, 'reg_date': datetime.date(2002, 3, 16), 'appl_date': datetime.date(2000, 11, 3), 'author_raw': 'Трифонов Сергей Владимирович (RU)\r\nБаурин Виктор Иванович (RU)\r\nФилина Людмила Петровна (RU)', 'owner_raw': 'Закрытое акционерное общество БЕЦЕМА (RU)', 'address': '', 'name': 'ПОЛУПРИЦЕП-ЦИСТЕРНА', 'actual': 'false', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'RU', 'region': None, 'city': None, 'author_count': 3}
{'reg_number': 50044, 'reg_date': datetime.date(2002, 3, 16), 'appl_date': datetime.date(2000, 6, 13), 'author_raw': 'Овчинников Михаил Михайлович (RU)\r\nСубботин Николай Иванович (RU)\r\nТиунов Олег Павлович (RU)\r\nКоротаев Юрий Леонидович (RU)', 'owner_raw': 'Общество с ограниченной ответственностью "АМТЕЛ-Русские шины"', 'address': 'ООО "АМТЕЛ-Русские шины", ул. 2-я Магистральная, 8А, стр.1, Москва, 123290', 'name': 'РИСУНОК ПРОТЕКТОРА', 'actual': 'false', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'RU', '

{'reg_number': 50406, 'reg_date': datetime.date(2002, 5, 16), 'appl_date': datetime.date(2001, 2, 19), 'author_raw': 'Карманов Виктор Сергеевич (RU)\r\nИванов Анатолий Александрович (RU)\r\nЛабунский Ростислав Юрьевич (RU)\r\nШмелева Алла Анатольевна (RU)', 'owner_raw': 'Открытое акционерное общество "Завод "ПРОММАШ" (RU)', 'address': '', 'name': 'ШКАФ ЖАРОЧНЫЙ ЭЛЕКТРИЧЕСКИЙ (два варианта)', 'actual': 'true', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'RU', 'region': None, 'city': None, 'author_count': 4}
{'reg_number': 50407, 'reg_date': datetime.date(2002, 5, 16), 'appl_date': datetime.date(2001, 12, 10), 'author_raw': 'Вихарев Дмитрий Владимирович (RU)', 'owner_raw': 'Автономная некоммерческая организация "РУССКИЙ КУБОК" (RU)', 'address': '127434, Москва, а/я 54, АООТ "Моспатент"', 'name': 'КУБОК "РУССКИЙ КУБОК"', 'actual': 'false', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'RU', 'region': 'МОСКВА', 'city': nan, 'author_count': 1}
{'reg

{'reg_number': 50744, 'reg_date': datetime.date(2002, 8, 16), 'appl_date': datetime.date(2001, 7, 12), 'author_raw': 'Малый Яков Григорьевич (RU)', 'owner_raw': 'Малый Яков Григорьевич (RU)', 'address': '', 'name': 'КОРСЕТ ГРУДОПОЯСНИЧНО-КРЕСТЦОВЫЙ ОРТОПЕДИЧЕСКИЙ', 'actual': 'false', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'RU', 'region': None, 'city': None, 'author_count': 1}
{'reg_number': 50745, 'reg_date': datetime.date(2002, 8, 16), 'appl_date': datetime.date(2001, 7, 12), 'author_raw': 'Малый Яков Григорьевич (RU)', 'owner_raw': 'Малый Яков Григорьевич (RU)', 'address': '', 'name': 'КОРСЕТ ГРУДОПОЯСНИЧНО-КРЕСТЦОВЫЙ ОРТОПЕДИЧЕСКИЙ', 'actual': 'false', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'RU', 'region': None, 'city': None, 'author_count': 1}
{'reg_number': 50746, 'reg_date': datetime.date(2002, 8, 16), 'appl_date': datetime.date(2001, 7, 12), 'author_raw': 'Малый Яков Григорьевич (RU)', 'owner_raw': 'Малый Яков Григорьевич (RU

{'reg_number': 51030, 'reg_date': datetime.date(2002, 9, 16), 'appl_date': datetime.date(2001, 11, 26), 'author_raw': 'Волжанин Николай Федорович (RU)\r\nИвойлов Михаил Германович (RU)\r\nЗагайнов Вениамин Федорович (RU)\r\nМусин Александр Разяпович (RU)\r\nРаннев Валерий Васильевич (RU)\r\nСалтыкова Ольга Олеговна (RU)\r\nУстюгов Владимир Сергеевич (RU)\r\nЧернов Михаил Павлович (RU)', 'owner_raw': 'Закрытое акционерное общество Специальное конструкторское бюро "Хроматэк" (RU)', 'address': '424006, Республика Марий Эл, г. Йошкар-Ола, а/я 33', 'name': 'ХРОМАТОГРАФ ГАЗОВЫЙ', 'actual': 'false', 'category': None, 'subcategory': None, 'kind': 3, 'country_code': 'RU', 'region': 'МАРИЙ ЭЛ РЕСПУБЛИКА', 'city': 'ЙОШКАР-ОЛА', 'author_count': 8}
{'reg_number': 51031, 'reg_date': datetime.date(2002, 9, 16), 'appl_date': datetime.date(2001, 4, 28), 'author_raw': 'Баранцев Петр Михайлович (RU)', 'owner_raw': 'Баранцев Петр Михайлович (RU)', 'address': '644060, г. Омск, а/я 1006, пат. пов. Т.А. Шишу

KeyboardInterrupt: 

In [1]:
import datetime
import pathlib

import pandas as pd

from app.parsers.common import format_tax_number


class PersonParser():
    CHUNKSIZE = 1e3
    IT_AC_CODES = ["62.01", "62.02", "62.02.1", "62.02.4", "62.03.13", "62.09", "63.11.1"]

    def __init__(self, df_path: pathlib.Path):
        self._df_path = df_path

    def _get_category(self, name: str, activity_code: str) -> str:
        if activity_code in self.IT_AC_CODES:
            return "ИТ-компания"

        return "Прочие организации"

    def _parse_row(self, row: pd.Series) -> dict:
        row = row.fillna("")

        tax_number = format_tax_number(row["ИНН"])

        if row["ОКОПФ (расшифровка)"] == "Индивидуальные предприниматели":
            kind = 2
        else:
            kind = 1

        try:
            reg_date = datetime.datetime.fromisoformat(
                row["creation_date"]).date()
        except:
            reg_date = None

        category = self._get_category(row["Наименование полное"], row["ОКВЭД2"])

        return dict(
            kind=kind,
            tax_number=tax_number,
            full_name=row["Наименование полное"],
            short_name=row["Наименование краткое"],
            legal_address=row["Юр адрес"],
            fact_address=row["Факт адрес"],
            reg_date=reg_date,
            active=row["Компания действующая (1) или нет (0)"] == "1",
            category=category,
        )

    def parse(self):
        df = pd.read_csv(self._df_path, dtype=str, chunksize=self.CHUNKSIZE)

        for chunk in df:
            chunk.dropna(subset=["Наименование полное", "ИНН"], how="any", inplace=True)
            chunk = chunk.loc[chunk["Головная компания (1) или филиал (0)"] == '1', :].copy()
            chunk.drop_duplicates(subset=["ИНН"], inplace=True)

            for _, row in chunk.iterrows():
                data = self._parse_row(row)
                yield data

    def setup(self):
        print("Setting up parser")
        df = pd.read_csv(self._df, chunksize=self.CHUNKSIZE)
        chunk = df.get_chunk(1)

        if "ИНН" not in chunk.columns:
            print("Column 'ИНН' not found in data")
            return False

        print("Data seems to be correct")

        return True

ModuleNotFoundError: No module named 'app'